In [2]:
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px


import numpy as np

from freq_stacking_LFM_ACF_utils import *

from scipy.fft import fft, ifft, fftfreq, fftshift
import scipy.signal

from tensorforce.environments import Environment
from tensorforce.agents import Agent


In [3]:
# min and max RF center freqs in Hz
fc_min = 500e6
fc_max = 1.48e9

delta_coeff = 0.01

# min and max Bws in Hz
Bmin = 10e6
Bmax = 20e6
delta_B = 1e6


max_delay_time = 5e-6
delay_time = 0.0

# chirp rate
chirp_rate = 50e6/10e-6


num_subpulses = 50

# maximum episode length
max_episode_timesteps = 3000

training_num = 200 # how many trajectories 

In [4]:
Fs_baseband = Bmax  # baseband samp freq in Hz
Fs_SWW_max = fc_max + Bmax / 2 - (fc_min - Bmax / 2)

# time window size
max_subpulse_duration = Bmax / chirp_rate
time_window_size = 10 * max_subpulse_duration + max_delay_time


# compute the state vector size
LFM_rx_subpulses, LFM_ref_subpulses = generate_LFM_rx_ref_subpulses_for_ACF(
    BW_RF_array=np.array([20e6]),
    chirp_rate=chirp_rate,
    time_window_size=time_window_size,
    Fs_baseband=Fs_baseband
)

N_max = compute_Nup_f(LFM_rx_subpulses[0], Fs_baseband, Fs_SWW_max) # the state vector size



In [5]:
# benchmark sww waveform
fc_RF_freqs = fc_min + np.arange(num_subpulses) * Bmin
BW_RF_array = Bmin * np.ones_like(fc_RF_freqs)

LFM_rx_subpulses, LFM_ref_subpulses = generate_LFM_rx_ref_subpulses_for_ACF(
    BW_RF_array, chirp_rate, time_window_size, Fs_baseband
)
# filter BWs
Bs_array = BW_RF_array

weights = np.ones(num_subpulses)
# apply freq. stacking
D_f, d_t = freq_stacking_v2(
    LFM_rx_subpulses,
    LFM_ref_subpulses,
    fc_RF_freqs,
    BW_RF_array,
    Bs_array,
    Fs_baseband,
    weights,
)

# compute times and freqs
f_RF_sww_center, BW_RF_sww = compute_para_for_RF_sww(fc_RF_freqs, BW_RF_array)
sww_samp_freq = BW_RF_sww


performance_benchmark = -int_sidelobe_ratio(np.abs(d_t))


times = fftshift(np.fft.fftfreq(n=D_f.size, d = sww_samp_freq) * D_f.size)
d_t[d_t == 0] = 1e-16 # to avoid divide by zero errors
norm_fac = np.max(np.abs(d_t))   
px.line(
    x = times,
    y= 20*np.log10( np.abs(d_t)  / norm_fac),
    labels={"x": "time", "y": "amplitude"},
    title=f"point spread function with ISLR = {performance_benchmark}",
)


In [6]:

freqs = fftshift(np.fft.fftfreq(n=D_f.size, d = 1/sww_samp_freq))

D_f[D_f == 0] = 1e-16 
norm_fac = np.max( np.abs(D_f) )
px.line(
    x = freqs,
    y= 20*np.log10(np.abs(D_f) / norm_fac),
    labels={"x": "time", "y": "amplitude"},
    title=f"Magnitude Spectrum of psf with ISLR = {performance_benchmark}",
)

In [7]:
# benchmark sww waveform
fc_RF_freqs = fc_min + np.arange(num_subpulses) * Bmin

BW_RF_array = np.array([1.2039454e+07, 1.0039454e+07, 1.2039454e+07, 1.2039454e+07,
        1.2039454e+07, 1.0039454e+07, 1.2039454e+07, 1.0039454e+07,
        1.0039454e+07, 1.0039454e+07, 1.0039454e+07, 1.0039454e+07,
        1.0039454e+07, 1.2039454e+07, 1.2039454e+07, 1.0039454e+07,
        1.2039454e+07, 1.0039454e+07, 1.0039454e+07, 1.0039454e+07,
        1.2039454e+07, 1.2039454e+07, 1.0039454e+07, 1.2039454e+07,
        1.0039454e+07, 1.2039454e+07, 1.0039454e+07, 1.0039454e+07,
        1.0039454e+07, 1.2039454e+07, 1.2039454e+07, 1.2039454e+07,
        1.0039454e+07, 1.0039454e+07, 1.0039454e+07, 1.0039454e+07,
        1.2039454e+07, 1.0039454e+07, 1.0039454e+07, 1.2039454e+07,
        1.2039454e+07, 1.2039454e+07, 1.0039454e+07, 1.2039454e+07,
        1.2039454e+07, 1.2039454e+07, 1.0039454e+07, 1.0039454e+07,
        1.0039454e+07, 1.2039454e+07])

LFM_rx_subpulses, LFM_ref_subpulses = generate_LFM_rx_ref_subpulses_for_ACF(
    BW_RF_array, chirp_rate, time_window_size, Fs_baseband
)
# filter BWs
Bs_array = BW_RF_array

weights = np.array([9.9000001e-01, 1.0000000e+00, 1.0000000e+00, 1.0000000e+00,
        1.0000000e+00, 1.0000000e+00, 1.0000000e+00, 1.0000000e+00,
        1.0000000e+00, 1.0000000e+00, 9.9000001e-01, 9.9000001e-01,
        9.9000001e-01, 9.9000001e-01, 9.9000001e-01, 9.9000001e-01,
        1.0000000e+00, 1.0000000e+00, 9.9000001e-01, 1.0000000e+00,
        1.0000000e+00, 9.9000001e-01, 1.0000000e+00, 9.9000001e-01,
        1.0000000e+00, 1.0000000e+00, 1.0000000e+00, 1.0000000e+00,
        9.9000001e-01, 9.9000001e-01, 1.0000000e+00, 9.9000001e-01,
        9.9000001e-01, 1.0000000e+00, 9.9000001e-01, 9.9000001e-01,
        9.9000001e-01, 1.0000000e+00, 9.9000001e-01, 1.0000000e+00,
        9.9000001e-01, 9.9000001e-01, 9.9000001e-01, 9.9000001e-01,
        1.0000000e+00, 9.9000001e-01, 9.9000001e-01, 9.9000001e-01,
        9.9000001e-01, 1.0000000e+00])
# apply freq. stacking
D_f_RL, d_t_RL = freq_stacking_v2(
    LFM_rx_subpulses,
    LFM_ref_subpulses,
    fc_RF_freqs,
    BW_RF_array,
    Bs_array,
    Fs_baseband,
    weights,
)



# compute times and freqs
f_RF_sww_center, BW_RF_sww = compute_para_for_RF_sww(fc_RF_freqs, BW_RF_array)
sww_samp_freq = BW_RF_sww


performance_benchmark = -int_sidelobe_ratio(np.abs(d_t_RL))


times = fftshift(np.fft.fftfreq(n=D_f_RL.size, d = sww_samp_freq) * D_f_RL.size)


norm_fac = np.max(np.abs(d_t_RL))
px.line(
    x = times,
    y= 20*np.log10(np.abs(d_t_RL) / norm_fac),
    labels={"x": "time", "y": "amplitude"},
    title=f"point spread function with ISLR = {performance_benchmark}",
)

In [8]:

freqs = fftshift(np.fft.fftfreq(n=D_f_RL.size, d = 1/sww_samp_freq))


D_f_RL[D_f_RL == 0] = 1e-16 # avoid divid by zero erros
norm_fac = np.max( np.abs(D_f_RL) )
px.line(
    x = freqs,
    y= 20*np.log10(np.abs(D_f_RL)/norm_fac),
    labels={"x": "time", "y": "amplitude"},
    title=f"Magnitude Spectrum of psf with ISLR = {performance_benchmark}",
)

In [9]:
from scipy import signal

win = signal.windows.hamming(d_t_RL.size)
D_f_RL_hamming_win = D_f_RL * win

In [13]:
d_t_RL_hamming = ifftshift(ifft(D_f_RL_hamming_win))

performance_benchmark = -int_sidelobe_ratio(np.abs(d_t_RL_hamming)) 

norm_fac = np.max( np.abs(d_t_RL_hamming) )
px.line(
    x = times,
    y= 20*np.log10(np.abs(d_t_RL_hamming) / norm_fac),
    labels={"x": "time", "y": "amplitude"},
    title=f"Magnitude Spectrum of psf with ISLR = {performance_benchmark}",
)